In [2]:
import pandas as pd

In [7]:
_dev = pd.read_json("EN_dev.jsonl", lines=True)
_test = pd.read_json("EN_test.jsonl", lines=True)
_train = pd.read_json("EN_train.jsonl", lines=True)

In [8]:
def process(df):
    df = df.copy()
    df.columns = df.columns.str.lower()
    df["violated"] = df.violated_articles.str.len() != 0
    return df

dev = process(_dev)
test = process(_test)
train = process(_train)

In [9]:
d = {k: list(v) for k, v in train.groupby("violated").indices.items()}
dist = dict(dev.violated.value_counts().items())
d_train = {k: v[0:dist[k]] for k, v in d.items()}
d_remaining = {k: v[dist[k]:] for k, v in d.items()}

new_rows = []
for label in dev["violated"]:
    new_rows.append(train.iloc[d_train[label].pop()])

new_train = pd.concat([pd.DataFrame(new_rows), pd.DataFrame(train.iloc[i] for l in d_remaining.values() for i in l).sample(frac=1, random_state=42)])

In [10]:
new_train.to_json("train.jsonl", lines=True, orient="records")
test.to_json("test.jsonl", lines=True, orient="records")
dev.to_json("dev.jsonl", lines=True, orient="records")

In [3]:
train = pd.read_json("data_anon/train.jsonl", lines=True, orient="records")
test = pd.read_json("data_anon/test.jsonl", lines=True, orient="records")
dev = pd.read_json("data_anon/dev.jsonl", lines=True, orient="records")

In [14]:
import re

number = re.compile("^([0-9]+|CARDINAL)\s?\. ")
train["text"] = train["text"].map(lambda r: [re.sub(number, "", line) for line in r])
test["text"] = test["text"].map(lambda r: [re.sub(number, "", line) for line in r])
dev["text"] = dev["text"].map(lambda r: [re.sub(number, "", line) for line in r])

In [ ]:
train.to_json("train.jsonl", lines=True, orient="records")
test.to_json("test.jsonl", lines=True, orient="records")
dev.to_json("dev.jsonl", lines=True, orient="records")